In [1]:
import cv2
from ultralytics import YOLO

class VehicleDetector:
    def __init__(self, model_path, min_vehicle_size=5000):
        self.model_path = model_path
        self.min_vehicle_size = min_vehicle_size
        self.model = YOLO(model_path)
        self.img_width = 1280  # 영상의 가로 해상도
        self.img_height = 720  # 영상의 세로 해상도
        self.center_line_x = self.img_width // 2  # 영상의 중앙선 x 좌표
        self.center_line_tolerance = 70  # 중앙선 허용 오차
    def check_front_vehicle(self, frame):
        # 중앙선을 통과하고 크기가 적절한 바운딩 박스만 필터링
        frame = cv2.resize(frame, (self.img_width, self.img_height))
        results = self.model.track(frame, persist=True)

        is_crash = 0  # 초기 값 설정
        x1, y1, x2, y2 = 0, 0, 0, 0  # 초기 값 설정

        for box in results[0].boxes:
            # 바운딩 박스의 중심 좌표 계산
            x_center = (box.xyxy[0][0] + box.xyxy[0][2]) // 2
            y_center = (box.xyxy[0][1] + box.xyxy[0][3]) // 2
            # 중앙선을 통과하는지 확인
            if self.center_line_x - self.center_line_tolerance < x_center < self.center_line_x + self.center_line_tolerance:
                # 바운딩 박스의 크기 계산
                box_size = box.xywh[0][2] * box.xywh[0][3]
                print(box_size, "인식이 되었습니다~~~~~~")
                # 자동차 클래스 필터링 및 크기 조건 검사
                confidence = box.conf.item()  # 텐서를 스칼라 값으로 변환
                label = f'Car: {confidence:.2f}'
                x1, y1, x2, y2 = map(int, box.xyxy[0])

                if 20000 < box_size < 80000:
                    is_crash = 1  # 전방 차량이 감지됨

                # 바운딩 박스 크기가 특정 값 이상인 경우
                elif box_size > 80000:
                    is_crash = 2  # 전방 차량이 감지됨 충돌 직전

        return is_crash, x1, y1, x2, y2  # 전방 차량이 감지되지 않음


def main(video_path, model_path):
    cap = cv2.VideoCapture(video_path)
    vehicle_detector = VehicleDetector(model_path)  # 차량 감지 클래스 초기화

    frame_count = 0
    while cap.isOpened():
        success, frame = cap.read()
        if not success:
            break

        frame_count += 1
        is_crash, x1, y1, x2, y2 = vehicle_detector.check_front_vehicle(frame)
        # 바운딩 박스 색상 설정
        color = (0, 255, 0)  # 초록색

        if is_crash == 1:
            color = (0, 165, 255)  # 주황색
        elif is_crash == 2:
            
            color = (0, 0, 255)  # 빨간색

        # 바운딩 박스 그리기
        cv2.rectangle(frame, (x1, y1), (x2, y2), color, 2)

        # 주행 상태 출력
        status = "Pass" if is_crash == 0 else "Fail"
        cv2.putText(frame, f"Status: {status}", (1000, 50), cv2.FONT_HERSHEY_SIMPLEX, 1, color, 2, cv2.LINE_AA)

        cv2.imshow("Frame", frame)
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break

    cap.release()
    cv2.destroyAllWindows()

if __name__ == "__main__":
    video_path = "/home/min/dev_ws/machine_learning/project_3rd/data/TEST_VIDEO/6_Fail_Pedestrian_Red_Light.MOV"
    model_path = "/home/min/dev_ws/machine_learning/project_3rd/src/judge_video/lane_detect/yolov8n.pt"
    main(video_path, model_path)



0: 384x640 2 cars, 1 bus, 1 truck, 238.0ms
Speed: 4.3ms preprocess, 238.0ms inference, 884.2ms postprocess per image at shape (1, 3, 384, 640)


QFactoryLoader::QFactoryLoader() checking directory path "/home/min/venv/yolo/lib/python3.10/site-packages/cv2/qt/plugins" ...
QFactoryLoader::QFactoryLoader() checking directory path "/usr/bin" ...
QFactoryLoader::QFactoryLoader() looking at "/usr/bin/411toppm"
"Failed to extract plugin meta data from '/usr/bin/411toppm'" 
         not a plugin
QFactoryLoader::QFactoryLoader() looking at "/usr/bin/7z"
QElfParser: '/usr/bin/7z' is not an ELF object (file too small)
"'/usr/bin/7z' is not an ELF object (file too small)" 
         not a plugin
QFactoryLoader::QFactoryLoader() looking at "/usr/bin/7za"
QElfParser: '/usr/bin/7za' is not an ELF object (file too small)
"'/usr/bin/7za' is not an ELF object (file too small)" 
         not a plugin
QFactoryLoader::QFactoryLoader() looking at "/usr/bin/7zr"
QElfParser: '/usr/bin/7zr' is not an ELF object (file too small)
"'/usr/bin/7zr' is not an ELF object (file too small)" 
         not a plugin
QFactoryLoader::QFactoryLoader() looking at "/usr


0: 384x640 2 cars, 1 bus, 1 truck, 11.5ms
Speed: 6.5ms preprocess, 11.5ms inference, 2.0ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 3 cars, 1 bus, 8.5ms
Speed: 1.7ms preprocess, 8.5ms inference, 1.4ms postprocess per image at shape (1, 3, 384, 640)
tensor(465.9974, device='cuda:0') 인식이 되었습니다~~~~~~

0: 384x640 3 cars, 2 buss, 9.9ms
Speed: 4.3ms preprocess, 9.9ms inference, 1.7ms postprocess per image at shape (1, 3, 384, 640)
tensor(563.4299, device='cuda:0') 인식이 되었습니다~~~~~~
tensor(333.3487, device='cuda:0') 인식이 되었습니다~~~~~~

0: 384x640 1 person, 4 cars, 1 bus, 1 truck, 10.1ms
Speed: 4.7ms preprocess, 10.1ms inference, 1.8ms postprocess per image at shape (1, 3, 384, 640)
tensor(606.3129, device='cuda:0') 인식이 되었습니다~~~~~~
tensor(396.2968, device='cuda:0') 인식이 되었습니다~~~~~~
tensor(369.0203, device='cuda:0') 인식이 되었습니다~~~~~~

0: 384x640 2 persons, 2 cars, 4 buss, 1 truck, 8.8ms
Speed: 4.3ms preprocess, 8.8ms inference, 1.7ms postprocess per image at shape (1, 3, 3

객체 인식은 됐고~ 이제 주행상태 판별하자

In [1]:
import cv2
from ultralytics import YOLO

class VehicleDetector:
    def __init__(self, model_path, min_vehicle_size=1000):
        self.model_path = model_path
        self.min_vehicle_size = min_vehicle_size
        self.model = YOLO(model_path)
        self.img_width = 1280  # 영상의 가로 해상도
        self.img_height = 720  # 영상의 세로 해상도
        self.center_line_x = self.img_width // 2  # 영상의 중앙선 x 좌표
        self.center_line_tolerance = 70  # 중앙선 허용 오차
        self.last_bbox_size = 0

    def check_front_vehicle(self, frame):
        frame = cv2.resize(frame, (self.img_width, self.img_height))
        results = self.model.track(frame, persist=True)

        is_crash = 0  # 초기 값 설정
        x1, y1, x2, y2 = 0, 0, 0, 0  # 초기 값 설정

        for box in results[0].boxes:
            # 바운딩 박스의 중심 좌표 계산
            x_center = (box.xyxy[0][0] + box.xyxy[0][2]) // 2
            y_center = (box.xyxy[0][1] + box.xyxy[0][3]) // 2
            # 중앙선을 통과하는지 확인
            if self.center_line_x - self.center_line_tolerance < x_center < self.center_line_x + self.center_line_tolerance:
                # 바운딩 박스의 크기 계산
                box_size = box.xywh[0][2] * box.xywh[0][3]
                # 자동차 클래스 필터링 및 크기 조건 검사
                if 20000 < box_size < 80000:
                    is_crash = 1  # 전방 차량이 감지됨
                elif box_size > 80000:
                    is_crash = 2  # 전방 차량이 감지됨 충돌 직전
                x1, y1, x2, y2 = map(int, box.xyxy[0])
                break  # 첫 번째 바운딩 박스만 고려

        return is_crash, x1, y1, x2, y2  # 전방 차량이 감지되지 않음

    def determine_driving_status(self, current_bbox_size):
        # 이전 프레임과의 바운딩 박스 크기 비교
        size_difference = abs(current_bbox_size - self.last_bbox_size)
        # 크기 변화량을 기준으로 주행 상태 판단
        if size_difference > 1000:  # 예시로 1000을 기준으로 주행 중으로 판단
            return True  # 주행 중
        else:
            return False  # 정지 중

    def update_last_bbox_size(self, current_bbox_size):
        self.last_bbox_size = current_bbox_size
import cv2

def main(video_path, model_path):
    cap = cv2.VideoCapture(video_path)
    vehicle_detector = VehicleDetector(model_path)  # 차량 감지 클래스 초기화

    frame_count = 0
    while cap.isOpened():
        success, frame = cap.read()
        if not success:
            break
        
        frame_count += 1
        is_crash, x1, y1, x2, y2 = vehicle_detector.check_front_vehicle(frame)
        
        # 바운딩 박스 색상 설정
        color = (0, 255, 0)  # 초록색
        if is_crash == 1:
            color = (0, 165, 255)  # 주황색
        elif is_crash == 2:
            color = (0, 0, 255)  # 빨간색

        # 바운딩 박스 그리기
        cv2.rectangle(frame, (x1, y1), (x2, y2), color, 2)
        
        # 주행 상태 판별 및 업데이트
        current_bbox_size = (x2 - x1) * (y2 - y1)
        is_driving = vehicle_detector.determine_driving_status(current_bbox_size)
        vehicle_detector.update_last_bbox_size(current_bbox_size)

        # 주행 상태에 따라 표시할 메시지 설정
        status_msg = "Driving" if is_driving else "Stopped"
        status_color = (0, 0, 255) if is_driving else (0, 255, 0)

        # 화면에 주행 상태 출력
        cv2.putText(frame, f"Status: {status_msg}", (1000, 50), cv2.FONT_HERSHEY_SIMPLEX, 1, status_color, 2, cv2.LINE_AA)

        # 화면에 출력
        cv2.imshow("Frame", frame)
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break

    cap.release()
    cv2.destroyAllWindows()

if __name__ == "__main__":
    video_path = "/home/min/dev_ws/machine_learning/project_3rd/data/TEST_VIDEO/6_Fail_Pedestrian_Red_Light.MOV"
    model_path = "/home/min/dev_ws/machine_learning/project_3rd/src/judge_video/lane_detect/yolov8n.pt"
    main(video_path, model_path)



0: 384x640 2 cars, 1 bus, 1 truck, 184.7ms
Speed: 2.5ms preprocess, 184.7ms inference, 989.5ms postprocess per image at shape (1, 3, 384, 640)


QFactoryLoader::QFactoryLoader() checking directory path "/home/min/venv/yolo/lib/python3.10/site-packages/cv2/qt/plugins" ...
QFactoryLoader::QFactoryLoader() checking directory path "/usr/bin" ...
QFactoryLoader::QFactoryLoader() looking at "/usr/bin/411toppm"
"Failed to extract plugin meta data from '/usr/bin/411toppm'" 
         not a plugin
QFactoryLoader::QFactoryLoader() looking at "/usr/bin/7z"
QElfParser: '/usr/bin/7z' is not an ELF object (file too small)
"'/usr/bin/7z' is not an ELF object (file too small)" 
         not a plugin
QFactoryLoader::QFactoryLoader() looking at "/usr/bin/7za"
QElfParser: '/usr/bin/7za' is not an ELF object (file too small)
"'/usr/bin/7za' is not an ELF object (file too small)" 
         not a plugin
QFactoryLoader::QFactoryLoader() looking at "/usr/bin/7zr"
QElfParser: '/usr/bin/7zr' is not an ELF object (file too small)
"'/usr/bin/7zr' is not an ELF object (file too small)" 
         not a plugin
QFactoryLoader::QFactoryLoader() looking at "/usr


0: 384x640 2 cars, 1 bus, 1 truck, 6.8ms
Speed: 3.3ms preprocess, 6.8ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 3 cars, 1 bus, 9.4ms
Speed: 2.4ms preprocess, 9.4ms inference, 1.7ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 3 cars, 2 buss, 10.5ms
Speed: 5.0ms preprocess, 10.5ms inference, 1.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 4 cars, 1 bus, 1 truck, 11.8ms
Speed: 4.4ms preprocess, 11.8ms inference, 1.3ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 2 cars, 4 buss, 1 truck, 11.3ms
Speed: 1.9ms preprocess, 11.3ms inference, 1.3ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 8 cars, 1 truck, 7.3ms
Speed: 1.8ms preprocess, 7.3ms inference, 1.4ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 6 cars, 1 traffic light, 8.4ms
Speed: 5.0ms preprocess, 8.4ms inference, 2.1ms postprocess per image at shape (1, 3, 384, 640)

In [5]:
import cv2

def main(video_path, model_path):
    cap = cv2.VideoCapture(video_path)
    vehicle_detector = VehicleDetector(model_path)  # 차량 감지 클래스 초기화
    df_data = []
    frame_count = 0
    while cap.isOpened():
        success, frame = cap.read()
        if not success:
            break
        
        frame_count += 1
        is_crash, x1, y1, x2, y2 = vehicle_detector.check_front_vehicle(frame)
        
        # 바운딩 박스 색상 설정
        color = (0, 255, 0)  # 초록색
        if is_crash == 1:
            color = (0, 165, 255)  # 주황색
        elif is_crash == 2:
            color = (0, 0, 255)  # 빨간색

        # 바운딩 박스 그리기
        cv2.rectangle(frame, (x1, y1), (x2, y2), color, 2)
        
        # 주행 상태 판별 및 업데이트
        if is_crash == 2:  # 충돌 직전인 경우에만 주행 상태를 판별하고 출력하고 저장
            current_bbox_size = (x2 - x1) * (y2 - y1)
            is_driving = vehicle_detector.determine_driving_status(current_bbox_size)
            vehicle_detector.update_last_bbox_size(current_bbox_size)

            # 주행 상태에 따라 표시할 메시지 설정
            status_msg = "Driving" if is_driving else "Stopped"
            status_color = (0, 0, 255) if is_driving else (0, 255, 0)

            # 화면에 주행 상태 출력
            cv2.putText(frame, f"Status: {status_msg}", (1000, 50), cv2.FONT_HERSHEY_SIMPLEX, 1, status_color, 2, cv2.LINE_AA)

        # 화면에 출력
        cv2.imshow("Frame", frame)
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break

    cap.release()
    cv2.destroyAllWindows()

if __name__ == "__main__":
    video_path = "/home/min/dev_ws/machine_learning/project_3rd/data/TEST_VIDEO/6_Fail_Pedestrian_Red_Light.MOV"
    model_path = "/home/min/dev_ws/machine_learning/project_3rd/src/judge_video/lane_detect/yolov8n.pt"
    main(video_path, model_path)



0: 384x640 2 cars, 1 bus, 1 truck, 7.1ms
Speed: 4.3ms preprocess, 7.1ms inference, 1.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 cars, 1 bus, 1 truck, 8.7ms
Speed: 3.1ms preprocess, 8.7ms inference, 2.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 3 cars, 1 bus, 10.8ms
Speed: 2.8ms preprocess, 10.8ms inference, 3.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 3 cars, 2 buss, 9.4ms
Speed: 4.7ms preprocess, 9.4ms inference, 2.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 4 cars, 1 bus, 1 truck, 8.8ms
Speed: 2.7ms preprocess, 8.8ms inference, 1.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 2 cars, 4 buss, 1 truck, 8.7ms
Speed: 3.5ms preprocess, 8.7ms inference, 1.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 8 cars, 1 truck, 7.5ms
Speed: 3.4ms preprocess, 7.5ms inference, 1.4ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 

위에꺼는 마무리 됐는데 이제!! 데이터 프레임에 저장해보자!!!

In [3]:
import cv2
import pandas as pd
from ultralytics import YOLO

class VehicleDetector:
    def __init__(self, model_path, min_vehicle_size=1000):
        self.model_path = model_path
        self.min_vehicle_size = min_vehicle_size
        self.model = YOLO(model_path)
        self.img_width = 1280  # 영상의 가로 해상도
        self.img_height = 720  # 영상의 세로 해상도
        self.center_line_x = self.img_width // 2  # 영상의 중앙선 x 좌표
        self.center_line_tolerance = 70  # 중앙선 허용 오차
        self.last_bbox_size = 0
        self.classes = {
            0: 'Car',
            1: 'Truck',
            2: 'Bus',
            # Add more classes if needed
        }

    def check_front_vehicle(self, frame):
        frame = cv2.resize(frame, (self.img_width, self.img_height))
        results = self.model.track(frame, persist=True)

        is_crash = 0  # 초기 값 설정
        x1, y1, x2, y2, class_id = 0, 0, 0, 0, 0  # 초기 값 설정

        for box in results[0].boxes:
            # 바운딩 박스의 중심 좌표 계산
            x_center = (box.xyxy[0][0] + box.xyxy[0][2]) // 2
            y_center = (box.xyxy[0][1] + box.xyxy[0][3]) // 2
            # 중앙선을 통과하는지 확인
            if self.center_line_x - self.center_line_tolerance < x_center < self.center_line_x + self.center_line_tolerance:
                # 바운딩 박스의 크기 계산
                box_size = box.xywh[0][2] * box.xywh[0][3]
                # 자동차 클래스 필터링 및 크기 조건 검사
                if 20000 < box_size < 80000:
                    is_crash = 1  # 전방 차량이 감지됨
                elif box_size > 80000:
                    is_crash = 2  # 전방 차량이 감지됨 충돌 직전
                x1, y1, x2, y2 = map(int, box.xyxy[0])
                class_id = int(box.cls[0])  # 클래스 ID 추출
                break  # 첫 번째 바운딩 박스만 고려

        return is_crash, x1, y1, x2, y2, class_id

    def determine_driving_status(self, current_bbox_size):
        # 이전 프레임과의 바운딩 박스 크기 비교
        size_difference = abs(current_bbox_size - self.last_bbox_size)
        # 크기 변화량을 기준으로 주행 상태 판단
        if size_difference > 1000:  # 예시로 1000을 기준으로 주행 중으로 판단
            return True  # 주행 중
        else:
            return False  # 정지 중

    def update_last_bbox_size(self, current_bbox_size):
        self.last_bbox_size = current_bbox_size

def main(video_path, model_path):
    cap = cv2.VideoCapture(video_path)
    vehicle_detector = VehicleDetector(model_path)  # 차량 감지 클래스 초기화
    df_data = []
    frame_count = 0
    while cap.isOpened():
        success, frame = cap.read()
        if not success:
            break
        
        frame_count += 1
        is_crash, x1, y1, x2, y2, class_id = vehicle_detector.check_front_vehicle(frame)
        
        # 바운딩 박스 색상 설정
        color = (0, 255, 0)  # 초록색
        if is_crash == 1:
            color = (0, 165, 255)  # 주황색
        elif is_crash == 2:
            color = (0, 0, 255)  # 빨간색

        # 바운딩 박스 그리기
        cv2.rectangle(frame, (x1, y1), (x2, y2), color, 2)
        
        # 주행 상태 판별 및 업데이트
        if is_crash == 2:  # 충돌 직전인 경우에만 주행 상태를 판별하고 출력하고 저장
            current_bbox_size = (x2 - x1) * (y2 - y1)
            is_driving = vehicle_detector.determine_driving_status(current_bbox_size)
            vehicle_detector.update_last_bbox_size(current_bbox_size)

            # 주행 상태에 따라 표시할 메시지 설정
            status_msg = "Driving" if is_driving else "Stopped"
            status_color = (0, 0, 255) if is_driving else (0, 255, 0)
            pass_fail = "Fail" if is_driving else "Pass"

            # 화면에 주행 상태 출력
            cv2.putText(frame, f"Status: {status_msg}", (1000, 50), cv2.FONT_HERSHEY_SIMPLEX, 1, status_color, 2, cv2.LINE_AA)

            # 데이터프레임에 저장
            class_name = vehicle_detector.classes.get(class_id, "Unknown")
            df_data.append({'ID': class_id, 'Class': class_name, 'Driving Status': pass_fail})

        # 화면에 출력
        cv2.imshow("Frame", frame)
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break

    cap.release()
    cv2.destroyAllWindows()

    # 데이터프레임 생성
    df = pd.DataFrame(df_data)

    # 데이터프레임 출력
    print(df)
    # 데이터프레임을 CSV 파일로 저장
    df.to_csv('vehicle_detection_results.csv', index=False)

if __name__ == "__main__":
    video_path = "/home/min/dev_ws/machine_learning/project_3rd/data/TEST_VIDEO/6_Fail_Pedestrian_Red_Light.MOV"
    model_path = "/home/min/dev_ws/machine_learning/project_3rd/src/judge_video/lane_detect/yolov8n.pt"
    main(video_path, model_path)



0: 384x640 2 cars, 1 bus, 1 truck, 178.5ms
Speed: 4.4ms preprocess, 178.5ms inference, 1058.9ms postprocess per image at shape (1, 3, 384, 640)


QFactoryLoader::QFactoryLoader() checking directory path "/home/min/venv/yolo/lib/python3.10/site-packages/cv2/qt/plugins" ...
QFactoryLoader::QFactoryLoader() checking directory path "/usr/bin" ...
QFactoryLoader::QFactoryLoader() looking at "/usr/bin/411toppm"
"Failed to extract plugin meta data from '/usr/bin/411toppm'" 
         not a plugin
QFactoryLoader::QFactoryLoader() looking at "/usr/bin/7z"
QElfParser: '/usr/bin/7z' is not an ELF object (file too small)
"'/usr/bin/7z' is not an ELF object (file too small)" 
         not a plugin
QFactoryLoader::QFactoryLoader() looking at "/usr/bin/7za"
QElfParser: '/usr/bin/7za' is not an ELF object (file too small)
"'/usr/bin/7za' is not an ELF object (file too small)" 
         not a plugin
QFactoryLoader::QFactoryLoader() looking at "/usr/bin/7zr"
QElfParser: '/usr/bin/7zr' is not an ELF object (file too small)
"'/usr/bin/7zr' is not an ELF object (file too small)" 
         not a plugin
QFactoryLoader::QFactoryLoader() looking at "/usr


0: 384x640 2 cars, 1 bus, 1 truck, 10.2ms
Speed: 6.1ms preprocess, 10.2ms inference, 2.1ms postprocess per image at shape (1, 3, 384, 640)



"Failed to extract plugin meta data from '/usr/bin/opal_wrapper'" 
         not a plugin
QFactoryLoader::QFactoryLoader() looking at "/usr/bin/mpiexec"
"Failed to extract plugin meta data from '/usr/bin/orterun'" 
         not a plugin
QFactoryLoader::QFactoryLoader() looking at "/usr/bin/mpiexec.openmpi"
"Failed to extract plugin meta data from '/usr/bin/orterun'" 
         not a plugin
QFactoryLoader::QFactoryLoader() looking at "/usr/bin/mpif77"
"Failed to extract plugin meta data from '/usr/bin/opal_wrapper'" 
         not a plugin
QFactoryLoader::QFactoryLoader() looking at "/usr/bin/mpif77.openmpi"
"Failed to extract plugin meta data from '/usr/bin/opal_wrapper'" 
         not a plugin
QFactoryLoader::QFactoryLoader() looking at "/usr/bin/mpif90"
"Failed to extract plugin meta data from '/usr/bin/opal_wrapper'" 
         not a plugin
QFactoryLoader::QFactoryLoader() looking at "/usr/bin/mpif90.openmpi"
"Failed to extract plugin meta data from '/usr/bin/opal_wrapper'" 
         no

0: 384x640 1 person, 3 cars, 1 bus, 6.3ms
Speed: 2.3ms preprocess, 6.3ms inference, 2.3ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 3 cars, 2 buss, 14.7ms
Speed: 5.3ms preprocess, 14.7ms inference, 2.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 4 cars, 1 bus, 1 truck, 14.6ms
Speed: 6.8ms preprocess, 14.6ms inference, 3.8ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 2 cars, 4 buss, 1 truck, 11.1ms
Speed: 3.1ms preprocess, 11.1ms inference, 2.4ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 8 cars, 1 truck, 14.0ms
Speed: 7.6ms preprocess, 14.0ms inference, 2.9ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 6 cars, 1 traffic light, 13.9ms
Speed: 5.3ms preprocess, 13.9ms inference, 3.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 10 cars, 1 truck, 11.1ms
Speed: 5.1ms preprocess, 11.1ms inference, 2.3ms postprocess per image at shape (1, 3, 384, 640)


In [1]:
import cv2
import pandas as pd
from ultralytics import YOLO

class VehicleDetector:
    def __init__(self, model_path, min_vehicle_size=1000):
        self.model_path = model_path
        self.min_vehicle_size = min_vehicle_size
        self.model = YOLO(model_path)
        self.img_width = 1280  # 영상의 가로 해상도
        self.img_height = 720  # 영상의 세로 해상도
        self.center_line_x = self.img_width // 2  # 영상의 중앙선 x 좌표
        self.center_line_tolerance = 70  # 중앙선 허용 오차
        self.last_bbox_size = 0
        self.classes = {
            0: 'Car',
            1: 'Truck',
            2: 'Bus',
            # Add more classes if needed
        }

    def check_front_vehicle(self, frame):
        frame = cv2.resize(frame, (self.img_width, self.img_height))
        results = self.model.track(frame, persist=True)

        is_crash = 0  # 초기 값 설정
        x1, y1, x2, y2, class_id = 0, 0, 0, 0, 0  # 초기 값 설정

        for box in results[0].boxes:
            # 바운딩 박스의 중심 좌표 계산
            x_center = (box.xyxy[0][0] + box.xyxy[0][2]) // 2
            y_center = (box.xyxy[0][1] + box.xyxy[0][3]) // 2
            # 중앙선을 통과하는지 확인
            if self.center_line_x - self.center_line_tolerance < x_center < self.center_line_x + self.center_line_tolerance:
                # 바운딩 박스의 크기 계산
                box_size = box.xywh[0][2] * box.xywh[0][3]
                # 자동차 클래스 필터링 및 크기 조건 검사
                if 20000 < box_size < 80000:
                    is_crash = 1  # 전방 차량이 감지됨
                elif box_size > 80000:
                    is_crash = 2  # 전방 차량이 감지됨 충돌 직전
                x1, y1, x2, y2 = map(int, box.xyxy[0])
                class_id = int(box.cls[0])  # 클래스 ID 추출
                print(box)
                break  # 첫 번째 바운딩 박스만 고려

        return is_crash, x1, y1, x2, y2, class_id

    def determine_driving_status(self, current_bbox_size):
        # 이전 프레임과의 바운딩 박스 크기 비교
        size_difference = abs(current_bbox_size - self.last_bbox_size)
        # 크기 변화량을 기준으로 주행 상태 판단
        if size_difference > 1000:  # 예시로 1000을 기준으로 주행 중으로 판단
            return True  # 주행 중
        else:
            return False  # 정지 중

    def update_last_bbox_size(self, current_bbox_size):
        self.last_bbox_size = current_bbox_size

def main(video_path, model_path):
    cap = cv2.VideoCapture(video_path)
    vehicle_detector = VehicleDetector(model_path)  # 차량 감지 클래스 초기화
    df_data = []
    frame_count = 0
    while cap.isOpened():
        success, frame = cap.read()
        if not success:
            break
        
        frame_count += 1
        is_crash, x1, y1, x2, y2, class_id = vehicle_detector.check_front_vehicle(frame)
        
        # 바운딩 박스 색상 설정
        color = (0, 255, 0)  # 초록색
        if is_crash == 1:
            color = (0, 165, 255)  # 주황색
        elif is_crash == 2:
            color = (0, 0, 255)  # 빨간색

        # 바운딩 박스 그리기
        cv2.rectangle(frame, (x1, y1), (x2, y2), color, 2)
        
        # 주행 상태 판별 및 업데이트
        if is_crash == 2:  # 충돌 직전인 경우에만 주행 상태를 판별하고 출력하고 저장
            current_bbox_size = (x2 - x1) * (y2 - y1)
            is_driving = vehicle_detector.determine_driving_status(current_bbox_size)
            vehicle_detector.update_last_bbox_size(current_bbox_size)

            # 주행 상태에 따라 표시할 메시지 설정
            status_msg = "Driving" if is_driving else "Stopped"
            status_color = (0, 0, 255) if is_driving else (0, 255, 0)
            pass_fail = "Fail" if is_driving else "Pass"

            # 화면에 주행 상태 출력
            cv2.putText(frame, f"ID: {class_id} Status: {status_msg} Pass/Fail: {pass_fail}", (20, 50), cv2.FONT_HERSHEY_SIMPLEX, 1, status_color, 2, cv2.LINE_AA)

            # 데이터프레임에 저장
            class_name = vehicle_detector.classes.get(class_id, "Unknown")
            df_data.append({'ID': class_id, 'Class': class_name, 'Driving Status': pass_fail})

        # 화면에 출력
        cv2.imshow("Frame", frame)
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break

    cap.release()
    cv2.destroyAllWindows()

    # 데이터프레임 생성
    df = pd.DataFrame(df_data)

    # 데이터프레임 출력
    print(df)
    # 데이터프레임을 CSV 파일로 저장
    df.to_csv('vehicle_detection_results.csv', index=False)

if __name__ == "__main__":
    video_path = "/home/min/dev_ws/machine_learning/project_3rd/data/TEST_VIDEO/6_Fail_Pedestrian_Red_Light.MOV"
    model_path = "/home/min/dev_ws/machine_learning/project_3rd/src/judge_video/lane_detect/yolov8n.pt"
    main(video_path, model_path)



0: 384x640 2 cars, 1 bus, 1 truck, 170.7ms
Speed: 4.0ms preprocess, 170.7ms inference, 1047.0ms postprocess per image at shape (1, 3, 384, 640)



QFactoryLoader::QFactoryLoader() checking directory path "/home/min/venv/yolo/lib/python3.10/site-packages/cv2/qt/plugins" ...
QFactoryLoader::QFactoryLoader() checking directory path "/usr/bin" ...
QFactoryLoader::QFactoryLoader() looking at "/usr/bin/411toppm"
"Failed to extract plugin meta data from '/usr/bin/411toppm'" 
         not a plugin
QFactoryLoader::QFactoryLoader() looking at "/usr/bin/7z"
QElfParser: '/usr/bin/7z' is not an ELF object (file too small)
"'/usr/bin/7z' is not an ELF object (file too small)" 
         not a plugin
QFactoryLoader::QFactoryLoader() looking at "/usr/bin/7za"
QElfParser: '/usr/bin/7za' is not an ELF object (file too small)
"'/usr/bin/7za' is not an ELF object (file too small)" 
         not a plugin
QFactoryLoader::QFactoryLoader() looking at "/usr/bin/7zr"
QElfParser: '/usr/bin/7zr' is not an ELF object (file too small)
"'/usr/bin/7zr' is not an ELF object (file too small)" 
         not a plugin
QFactoryLoader::QFactoryLoader() looking at "/usr

0: 384x640 2 cars, 1 bus, 1 truck, 10.8ms
Speed: 8.6ms preprocess, 10.8ms inference, 1.5ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 3 cars, 1 bus, 9.7ms
Speed: 2.3ms preprocess, 9.7ms inference, 2.6ms postprocess per image at shape (1, 3, 384, 640)
ultralytics.engine.results.Boxes object with attributes:

cls: tensor([2.], device='cuda:0')
conf: tensor([0.1036], device='cuda:0')
data: tensor([[5.6913e+02, 4.4171e+02, 5.9586e+02, 4.5914e+02, 1.0363e-01, 2.0000e+00]], device='cuda:0')
id: None
is_track: False
orig_shape: (720, 1280)
shape: torch.Size([1, 6])
xywh: tensor([[582.4988, 450.4239,  26.7314,  17.4326]], device='cuda:0')
xywhn: tensor([[0.4551, 0.6256, 0.0209, 0.0242]], device='cuda:0')
xyxy: tensor([[569.1331, 441.7076, 595.8645, 459.1402]], device='cuda:0')
xyxyn: tensor([[0.4446, 0.6135, 0.4655, 0.6377]], device='cuda:0')

0: 384x640 3 cars, 2 buss, 8.9ms
Speed: 5.9ms preprocess, 8.9ms inference, 2.7ms postprocess per image at shape (1, 3, 384, 6

track_id 당 값 하나씩만 저장하기!

In [2]:
import cv2
import pandas as pd
from ultralytics import YOLO

class VehicleDetector:
    def __init__(self, model_path, min_vehicle_size=1000):
        self.model_path = model_path
        self.min_vehicle_size = min_vehicle_size
        self.model = YOLO(model_path)
        self.img_width = 1280  # 영상의 가로 해상도
        self.img_height = 720  # 영상의 세로 해상도
        self.center_line_x = self.img_width // 2  # 영상의 중앙선 x 좌표
        self.center_line_tolerance = 70  # 중앙선 허용 오차
        self.last_bbox_size = 0
        self.classes = {
            0: 'Car',
            1: 'Truck',
            2: 'Bus',
            # Add more classes if needed
        }

    def check_front_vehicle(self, frame):
        frame = cv2.resize(frame, (self.img_width, self.img_height))
        results = self.model.track(frame, persist=True)

        is_crash = 0  # 초기 값 설정
        x1, y1, x2, y2, track_id = 0, 0, 0, 0, 0  # 초기 값 설정

        for box in results[0].boxes:
            # 바운딩 박스의 중심 좌표 계산
            x_center = (box.xyxy[0][0] + box.xyxy[0][2]) // 2
            y_center = (box.xyxy[0][1] + box.xyxy[0][3]) // 2
            # 중앙선을 통과하는지 확인
            if self.center_line_x - self.center_line_tolerance < x_center < self.center_line_x + self.center_line_tolerance:
                # 바운딩 박스의 크기 계산
                box_size = box.xywh[0][2] * box.xywh[0][3]
                # 자동차 클래스 필터링 및 크기 조건 검사
                if 20000 < box_size < 80000:
                    is_crash = 1  # 전방 차량이 감지됨
                elif box_size > 80000:
                    is_crash = 2  # 전방 차량이 감지됨 충돌 직전
                    if box.id is not None:  # None이 아닌 경우에만 track_id 설정
                        track_id = int(box.id)  # 클래스 ID 추출
                
                x1, y1, x2, y2 = map(int, box.xyxy[0])
                break  # 첫 번째 바운딩 박스만 고려

        return is_crash, x1, y1, x2, y2, track_id

    def determine_driving_status(self, current_bbox_size):
        # 이전 프레임과의 바운딩 박스 크기 비교
        size_difference = abs(current_bbox_size - self.last_bbox_size)
        # 크기 변화량을 기준으로 주행 상태 판단
        if size_difference > 1000:  # 예시로 1000을 기준으로 주행 중으로 판단
            return True  # 주행 중
        else:
            return False  # 정지 중

    def update_last_bbox_size(self, current_bbox_size):
        self.last_bbox_size = current_bbox_size

def main(video_path, model_path):
    cap = cv2.VideoCapture(video_path)
    vehicle_detector = VehicleDetector(model_path)  # 차량 감지 클래스 초기화
    df_data = []
    frame_count = 0
    while cap.isOpened():
        success, frame = cap.read()
        if not success:
            break
        
        frame_count += 1
        is_crash, x1, y1, x2, y2, track_id = vehicle_detector.check_front_vehicle(frame)
        
        # 바운딩 박스 색상 설정
        color = (0, 255, 0)  # 초록색
        if is_crash == 1:
            color = (0, 165, 255)  # 주황색
        elif is_crash == 2:
            color = (0, 0, 255)  # 빨간색

        # 바운딩 박스 그리기
        cv2.rectangle(frame, (x1, y1), (x2, y2), color, 2)
        
        # 주행 상태 판별 및 업데이트
        if is_crash == 2:  # 충돌 직전인 경우에만 주행 상태를 판별하고 출력하고 저장
            current_bbox_size = (x2 - x1) * (y2 - y1)
            is_driving = vehicle_detector.determine_driving_status(current_bbox_size)
            vehicle_detector.update_last_bbox_size(current_bbox_size)

            # 주행 상태에 따라 표시할 메시지 설정
            status_msg = "Driving" if is_driving else "Stopped"
            status_color = (0, 0, 255) if is_driving else (0, 255, 0)
            pass_fail = "Fail" if is_driving else "Pass"

            # 화면에 주행 상태 출력
            cv2.putText(frame, f"ID: {track_id} Status: {status_msg} Pass/Fail: {pass_fail}", (20, 50), cv2.FONT_HERSHEY_SIMPLEX, 1, status_color, 2, cv2.LINE_AA)

            # 데이터프레임에 저장
            class_name = vehicle_detector.classes.get(track_id, "Unknown")
            df_data.append({'ID': track_id, 'driving': status_msg, 'Pass/Fail': pass_fail})

        # 화면에 출력
        cv2.imshow("Frame", frame)
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break

    cap.release()
    cv2.destroyAllWindows()

    # 데이터프레임 생성
    df = pd.DataFrame(df_data)

    # 데이터프레임 출력
    print(df)
    # 데이터프레임을 CSV 파일로 저장
    df.to_csv('vehicle_detection_results.csv', index=False)

if __name__ == "__main__":
    video_path = "/home/min/dev_ws/machine_learning/project_3rd/data/TEST_VIDEO/6_Fail_Pedestrian_Red_Light.MOV"
    model_path = "/home/min/dev_ws/machine_learning/project_3rd/src/judge_video/lane_detect/yolov8n.pt"
    main(video_path, model_path)



0: 384x640 2 cars, 1 bus, 1 truck, 7.1ms
Speed: 2.2ms preprocess, 7.1ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 cars, 1 bus, 1 truck, 9.9ms
Speed: 3.4ms preprocess, 9.9ms inference, 2.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 3 cars, 1 bus, 8.0ms
Speed: 2.7ms preprocess, 8.0ms inference, 1.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 3 cars, 2 buss, 8.2ms
Speed: 3.8ms preprocess, 8.2ms inference, 1.4ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 4 cars, 1 bus, 1 truck, 9.4ms
Speed: 3.4ms preprocess, 9.4ms inference, 1.6ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 2 persons, 2 cars, 4 buss, 1 truck, 6.3ms
Speed: 2.4ms preprocess, 6.3ms inference, 1.5ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 person, 8 cars, 1 truck, 9.6ms
Speed: 2.7ms preprocess, 9.6ms inference, 1.1ms postprocess per image at shape (1, 3, 384, 640)

0: 384x640 1 pe

track_id마다 하나씩!

최종

In [12]:
import cv2
import pandas as pd
from collections import defaultdict, deque
from statistics import mode
from ultralytics import YOLO

class VehicleDetector:
    def __init__(self, model_path, min_vehicle_size=1000):
        self.model_path = model_path
        self.min_vehicle_size = min_vehicle_size
        self.model = YOLO(model_path)
        self.img_width = 1280  # 영상의 가로 해상도
        self.img_height = 720  # 영상의 세로 해상도
        self.center_line_x = self.img_width // 2  # 영상의 중앙선 x 좌표
        self.center_line_tolerance = 70  # 중앙선 허용 오차
        self.last_bbox_size = 0
        self.classes = {
            0: "person",
            2: "car",
            5: "bus",
            7: "truck",
            # Add more classes if needed
        }
        self.pass_fail_status_history = defaultdict(lambda: deque(maxlen=10))  # 최대 10개 항목 저장
        self.pass_fail_status = {}

    def check_front_vehicle(self, frame):
        frame = cv2.resize(frame, (self.img_width, self.img_height))
        results = self.model.track(frame, persist=True)

        is_crash = 0  # 초기 값 설정
        x1, y1, x2, y2, track_id, class_id = 0, 0, 0, 0, 0, 0  # 초기 값 설정

        for box in results[0].boxes:
            # 바운딩 박스의 중심 좌표 계산
            x_center = (box.xyxy[0][0] + box.xyxy[0][2]) // 2
            y_center = (box.xyxy[0][1] + box.xyxy[0][3]) // 2
            print(box)
            # 중앙선을 통과하는지 확인
            if self.center_line_x - self.center_line_tolerance < x_center < self.center_line_x + self.center_line_tolerance:
                # 바운딩 박스의 크기 계산
                box_size = box.xywh[0][2] * box.xywh[0][3]
                # 자동차 클래스 필터링 및 크기 조건 검사
                if 20000 < box_size < 80000:
                    is_crash = 1  # 전방 차량이 감지됨
                elif box_size > 80000:
                    is_crash = 2  # 전방 차량이 감지됨 충돌 직전
                    if box.id is not None:  # None이 아닌 경우에만 track_id 설정
                        track_id = int(box.id)  # 클래스 ID 추출
                        class_id = int(box.cls)
                
                x1, y1, x2, y2 = map(int, box.xyxy[0])
                break  # 첫 번째 바운딩 박스만 고려

        return is_crash, x1, y1, x2, y2, track_id, class_id

    def determine_driving_status(self, current_bbox_size):
        # 이전 프레임과의 바운딩 박스 크기 비교
        size_difference = abs(current_bbox_size - self.last_bbox_size)
        # 크기 변화량을 기준으로 주행 상태 판단
        if size_difference > 1000:  # 예시로 1000을 기준으로 주행 중으로 판단
            return True  # 주행 중
        else:
            return False  # 정지 중

    def update_last_bbox_size(self, current_bbox_size):
        self.last_bbox_size = current_bbox_size

    def determine_pass_fail_status(self, is_driving):
        return 'Fail' if is_driving else 'Pass'

def main(video_path, model_path):
    cap = cv2.VideoCapture(video_path)
    vehicle_detector = VehicleDetector(model_path)  # 차량 감지 클래스 초기화
    df_data = []
    frame_count = 0

    while cap.isOpened():
        success, frame = cap.read()
        if not success:
            break
        
        frame_count += 1
        is_crash, x1, y1, x2, y2, track_id, class_id = vehicle_detector.check_front_vehicle(frame)
        
        # 바운딩 박스 색상 설정
        color = (0, 255, 0)  # 초록색
        if is_crash == 1:
            color = (0, 165, 255)  # 주황색
        elif is_crash == 2:
            color = (0, 0, 255)  # 빨간색

        # 바운딩 박스 그리기
        cv2.rectangle(frame, (x1, y1), (x2, y2), color, 2)
        
        # 주행 상태 판별 및 업데이트
        if is_crash == 2:  # 충돌 직전인 경우에만 주행 상태를 판별하고 출력하고 저장
            current_bbox_size = (x2 - x1) * (y2 - y1)
            is_driving = vehicle_detector.determine_driving_status(current_bbox_size)
            vehicle_detector.update_last_bbox_size(current_bbox_size)

            if track_id:
                pass_fail = vehicle_detector.determine_pass_fail_status(is_driving)
                vehicle_detector.pass_fail_status_history[track_id].append(pass_fail)

                # 최종 10개 데이터 기반 판단
                if len(vehicle_detector.pass_fail_status_history[track_id]) == 10:
                    vehicle_detector.pass_fail_status[track_id] = mode(vehicle_detector.pass_fail_status_history[track_id])
                else:
                    vehicle_detector.pass_fail_status[track_id] = pass_fail

                # 주행 상태에 따라 표시할 메시지 설정
                status_msg = "Driving" if is_driving else "Stopped"
                pass_fail = vehicle_detector.pass_fail_status[track_id]

                # 화면에 주행 상태 출력
                cv2.putText(frame, f"ID: {track_id} Status: {status_msg} Pass/Fail: {pass_fail}", (20, 50), cv2.FONT_HERSHEY_SIMPLEX, 1, color, 2, cv2.LINE_AA)

                # 데이터프레임에 저장
                df_data.append({'Class_ID': class_id, 'driving': status_msg, 'Pass/Fail': pass_fail})

        # 화면에 출력
        cv2.imshow("Frame", frame)
        if cv2.waitKey(1) & 0xFF == ord('q'):
            break

    cap.release()
    cv2.destroyAllWindows()

    # 최종 데이터프레임 생성
    df = pd.DataFrame(df_data)

    # 중복된 ID에 대해 최다빈도수 값만 남기고 나머지는 제거
    df = df.groupby('ID').agg(lambda x: Counter(x).most_common(1)[0][0]).reset_index()

    # 데이터프레임 출력
    print(df)
    # 데이터프레임을 CSV 파일로 저장
    df.to_csv('vehicle_detection_results.csv', index=False)

if __name__ == "__main__":
    video_path = "/home/min/dev_ws/machine_learning/project_3rd/data/TEST_VIDEO/6_Fail_Pedestrian_Red_Light.MOV"
    model_path = "/home/min/dev_ws/machine_learning/project_3rd/src/judge_video/lane_detect/yolov8n.pt"
    main(video_path, model_path)



0: 384x640 2 cars, 1 bus, 1 truck, 10.5ms
Speed: 5.1ms preprocess, 10.5ms inference, 1.2ms postprocess per image at shape (1, 3, 384, 640)
ultralytics.engine.results.Boxes object with attributes:

cls: tensor([2.], device='cuda:0')
conf: tensor([0.3822], device='cuda:0')
data: tensor([[4.9132e+02, 4.3241e+02, 5.4865e+02, 4.6439e+02, 3.8217e-01, 2.0000e+00]], device='cuda:0')
id: None
is_track: False
orig_shape: (720, 1280)
shape: torch.Size([1, 6])
xywh: tensor([[519.9856, 448.3994,  57.3213,  31.9871]], device='cuda:0')
xywhn: tensor([[0.4062, 0.6228, 0.0448, 0.0444]], device='cuda:0')
xyxy: tensor([[491.3250, 432.4059, 548.6462, 464.3930]], device='cuda:0')
xyxyn: tensor([[0.3838, 0.6006, 0.4286, 0.6450]], device='cuda:0')
ultralytics.engine.results.Boxes object with attributes:

cls: tensor([2.], device='cuda:0')
conf: tensor([0.1921], device='cuda:0')
data: tensor([[7.3698e-01, 6.1000e+02, 2.1816e+02, 7.1647e+02, 1.9207e-01, 2.0000e+00]], device='cuda:0')
id: None
is_track: False
